In [1]:
from urllib.request import urlopen
import requests
from bs4 import BeautifulSoup as bts
import pandas as pd
import re
import time
import sys
from datetime import datetime
from datetime import date
import simplejson as json
import random

In [2]:
def getAndParseURL(url):
    result = requests.get(url,headers = {"User-Agent": 'Mozilla/5.0'})
    #result = requests.get(url,headers = {'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/73.0.3683.103 Safari/537.36'})
    #result = requests.get(url,headers = {'User-Agent': 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_10_1) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/73.0.3683.103 Safari/537.36'})
    soup = bts(result.text, 'html.parser')
    return soup

In [3]:
team_list = list()
html = getAndParseURL('https://fbref.com/en/comps/9/Premier-League-Stats')

for i in html.find_all("td",{"data-stat":"team"}):
    for j in i.find_all("a"):
        if "/en/stathead/matchup/teams/" not in j['href']:
            team_list.append(j['href'])
team_list

['/en/squads/18bb7c10/Arsenal-Stats',
 '/en/squads/b8fd03ef/Manchester-City-Stats',
 '/en/squads/19538871/Manchester-United-Stats',
 '/en/squads/361ca564/Tottenham-Hotspur-Stats',
 '/en/squads/b2b47a98/Newcastle-United-Stats',
 '/en/squads/fd962109/Fulham-Stats',
 '/en/squads/822bd0ba/Liverpool-Stats',
 '/en/squads/d07537b9/Brighton-and-Hove-Albion-Stats',
 '/en/squads/cd051869/Brentford-Stats',
 '/en/squads/cff3d9bb/Chelsea-Stats',
 '/en/squads/8602292d/Aston-Villa-Stats',
 '/en/squads/47c64c55/Crystal-Palace-Stats',
 '/en/squads/e4a775cb/Nottingham-Forest-Stats',
 '/en/squads/a2d435b3/Leicester-City-Stats',
 '/en/squads/8cec06e1/Wolverhampton-Wanderers-Stats',
 '/en/squads/7c21e445/West-Ham-United-Stats',
 '/en/squads/5bfb9659/Leeds-United-Stats',
 '/en/squads/d3fd31cc/Everton-Stats',
 '/en/squads/4ba7cbea/Bournemouth-Stats',
 '/en/squads/33c895d4/Southampton-Stats',
 '/en/squads/18bb7c10/Arsenal-Stats',
 '/en/squads/b8fd03ef/Manchester-City-Stats',
 '/en/squads/19538871/Manchester-U

In [4]:
matchReports_list = list()
for i in range(int(len(team_list)/2)):
    print(i+1, " / ",int(len(team_list)/2))
    html = getAndParseURL('https://fbref.com'+team_list[i])
    for i in html.find_all("td",{"data-stat":"match_report"}):
        for j in i.find_all("a"):
            if "/en/stathead/matchup/teams/" not in j['href']:
                matchReports_list.append(j['href'])
    time.sleep(random.randint(1,5))
matchReports_list

1  /  20
2  /  20
3  /  20
4  /  20
5  /  20
6  /  20
7  /  20
8  /  20
9  /  20
10  /  20
11  /  20
12  /  20
13  /  20
14  /  20
15  /  20
16  /  20
17  /  20
18  /  20
19  /  20
20  /  20


['/en/matches/e62f6e78/Crystal-Palace-Arsenal-August-5-2022-Premier-League',
 '/en/matches/7483b97f/Arsenal-Leicester-City-August-13-2022-Premier-League',
 '/en/matches/7f11dd9e/Bournemouth-Arsenal-August-20-2022-Premier-League',
 '/en/matches/8b69fd2d/Arsenal-Fulham-August-27-2022-Premier-League',
 '/en/matches/cc235aad/Arsenal-Aston-Villa-August-31-2022-Premier-League',
 '/en/matches/61ddafa5/Manchester-United-Arsenal-September-4-2022-Premier-League',
 '/en/matches/e77d99bf/Zurich-Arsenal-September-8-2022-Europa-League',
 '/en/matches/fd5626e6/Brentford-Arsenal-September-18-2022-Premier-League',
 '/en/matches/aefe3b90/North-London-Derby-Arsenal-Tottenham-Hotspur-October-1-2022-Premier-League',
 '/en/matches/91a1d3df/Arsenal-BodoGlimt-October-6-2022-Europa-League',
 '/en/matches/84a48413/Arsenal-Liverpool-October-9-2022-Premier-League',
 '/en/matches/04e59775/BodoGlimt-Arsenal-October-13-2022-Europa-League',
 '/en/matches/92885cfc/Leeds-United-Arsenal-October-16-2022-Premier-League',


In [5]:
# Defining of the dataframe
df = pd.DataFrame(columns=['matchReport_link','home_team','away_team','venue_date','player_team','player_name','shirtnumber', 'nationality', 'position', 'age', 'min_played', 'goals','assists',
                          'pens_made','pens_att','shots','shots_on_target','cards_yellow','cards_red','touches',
                          'tackles','interceptions','blocks','xg','npxg','xg_assist','sca','gca','passes_completed',
                          'passes','passes_pct','progressive_passes','carries','progressive_carries','take_ons',
                          'take_ons_won'])

In [6]:
for index in range(len(matchReports_list)):
#for index in range(1):
        print(index+1, " / ",len(matchReports_list))
        match_details = dict()
        #html = getAndParseURL('https://fbref.com/en/matches/25436a3b/Everton-Aston-Villa-February-25-2023-Premier-League')
        html = getAndParseURL('https://fbref.com' + matchReports_list[index])
        matchReport_link = ('https://fbref.com' + matchReports_list[index])

        #Scraping the name of the teams and competition
        temp = list()
        for i in html.find_all("div",{"class":"scorebox"}):
            for j in i.find_all("a"):
                temp.append(j.text)
        home_team = temp[0]
        if temp[4] == 'Prev Match':
            away_team = temp[3]
        else:
            away_team = temp[4]

        #Scraping the date and the time of the venue
        el = html.find("span",{"class":"venuetime"})
        venue_date = el['data-venue-date']
        
        table_list = html.find_all('table', class_='stats_table sortable')
        if len(table_list) >= 6:
            home_table = table_list[0]
            away_table = table_list[6]


            # Collecting home team data
            for row in home_table.tbody.find_all('tr'):    
                columns = row.find_all('td')
                player_name = row.find_all('a')[0].text

                if(columns != []):
                    shirtnumber = columns[0].text.strip()
                    try:
                        nationality = columns[1].text.split()[1].strip()
                    except:
                        nationality = None
                    position = columns[2].text.strip()
                    try:
                        age = int(columns[3].text.split("-")[0].strip()) + int(columns[3].text.split("-")[1].strip())/365
                    except:
                        age = None
                    min_played = columns[4].text.strip()
                    goals = columns[5].text.strip()
                    assists = columns[6].text.strip()
                    pens_made = columns[7].text.strip()
                    pens_att = columns[8].text.strip()
                    shots = columns[9].text.strip()
                    shots_on_target = columns[10].text.strip()
                    cards_yellow = columns[11].text.strip()
                    cards_red = columns[12].text.strip()
                    touches = columns[13].text.strip()
                    tackles = columns[14].text.strip()
                    interceptions = columns[15].text.strip()
                    blocks = columns[16].text.strip()
                    xg = columns[17].text.strip()
                    npxg = columns[18].text.strip()
                    xg_assist = columns[19].text.strip()
                    sca = columns[20].text.strip()
                    gca = columns[21].text.strip()
                    passes_completed = columns[22].text.strip()
                    passes = columns[23].text.strip()
                    passes_pct = columns[24].text.strip()
                    progressive_passes = columns[25].text.strip()
                    carries = columns[26].text.strip()
                    progressive_carries = columns[27].text.strip()
                    take_ons = columns[28].text.strip()
                    take_ons_won = columns[29].text.strip()

                    df = df.append({'matchReport_link':matchReport_link,'home_team': home_team,'away_team': away_team,'venue_date': venue_date,'player_team': home_team,
                                    'player_name': player_name,'shirtnumber': shirtnumber,  'nationality': nationality, 'position': position,
                                    'age': age, 'min_played': min_played, 'goals': goals, 'assists': assists, 'pens_made': pens_made
                                   , 'pens_att': pens_att, 'shots': shots, 'shots_on_target': shots_on_target, 'cards_yellow': cards_yellow
                                   , 'cards_red': cards_red, 'touches': touches, 'tackles': tackles, 'interceptions': interceptions
                                   , 'blocks': blocks, 'xg': xg, 'npxg': npxg, 'xg_assist': xg_assist, 'sca': sca
                                   , 'gca': gca, 'passes_completed': passes_completed, 'passes': passes, 'passes_pct': passes_pct
                                   , 'progressive_passes': progressive_passes, 'carries': carries, 'progressive_carries': progressive_carries
                                    , 'take_ons': take_ons, 'take_ons_won': take_ons_won}, ignore_index=True)
            # Collecting away team data
            for row in away_table.tbody.find_all('tr'):
                columns = row.find_all('td')
                player_name = row.find_all('a')[0].text

                if(columns != []):
                    shirtnumber = columns[0].text.strip()
                    try:
                        nationality = columns[1].text.split()[1].strip()
                    except:
                        nationality = None
                    position = columns[2].text.strip()
                    try:
                        age = int(columns[3].text.split("-")[0].strip()) + int(columns[3].text.split("-")[1].strip())/365
                    except:
                        age = None
                    min_played = columns[4].text.strip()
                    goals = columns[5].text.strip()
                    assists = columns[6].text.strip()
                    pens_made = columns[7].text.strip()
                    pens_att = columns[8].text.strip()
                    shots = columns[9].text.strip()
                    shots_on_target = columns[10].text.strip()
                    cards_yellow = columns[11].text.strip()
                    cards_red = columns[12].text.strip()
                    touches = columns[13].text.strip()
                    tackles = columns[14].text.strip()
                    interceptions = columns[15].text.strip()
                    blocks = columns[16].text.strip()
                    xg = columns[17].text.strip()
                    npxg = columns[18].text.strip()
                    xg_assist = columns[19].text.strip()
                    sca = columns[20].text.strip()
                    gca = columns[21].text.strip()
                    passes_completed = columns[22].text.strip()
                    passes = columns[23].text.strip()
                    passes_pct = columns[24].text.strip()
                    progressive_passes = columns[25].text.strip()
                    carries = columns[26].text.strip()
                    progressive_carries = columns[27].text.strip()
                    take_ons = columns[28].text.strip()
                    take_ons_won = columns[29].text.strip()

                    df = df.append({'matchReport_link':matchReport_link,'home_team': home_team,'away_team': away_team,'venue_date': venue_date,'player_team': away_team,
                                'player_name': player_name,'shirtnumber': shirtnumber,  'nationality': nationality, 'position': position,
                                'age': age, 'min_played': min_played, 'goals': goals, 'assists': assists, 'pens_made': pens_made
                               , 'pens_att': pens_att, 'shots': shots, 'shots_on_target': shots_on_target, 'cards_yellow': cards_yellow
                               , 'cards_red': cards_red, 'touches': touches, 'tackles': tackles, 'interceptions': interceptions
                               , 'blocks': blocks, 'xg': xg, 'npxg': npxg, 'xg_assist': xg_assist, 'sca': sca
                               , 'gca': gca, 'passes_completed': passes_completed, 'passes': passes, 'passes_pct': passes_pct
                               , 'progressive_passes': progressive_passes, 'carries': carries, 'progressive_carries': progressive_carries
                                , 'take_ons': take_ons, 'take_ons_won': take_ons_won}, ignore_index=True)
        else:
            home_table = table_list[0]
            away_table = table_list[1]


            # Collecting home team data
            for row in home_table.tbody.find_all('tr'):    
                columns = row.find_all('td')
                player_name = row.find_all('a')[0].text

                if(columns != []):
                    shirtnumber = columns[0].text.strip()
                    try:
                        nationality = columns[1].text.split()[1].strip()
                    except:
                        nationality = None
                    position = columns[2].text.strip()
                    try:
                        age = int(columns[3].text.split("-")[0].strip()) + int(columns[3].text.split("-")[1].strip())/365
                    except:
                        age = None
                    min_played = columns[4].text.strip()
                    goals = columns[5].text.strip()
                    assists = columns[6].text.strip()
                    pens_made = columns[7].text.strip()
                    pens_att = columns[8].text.strip()
                    shots = columns[9].text.strip()
                    shots_on_target = columns[10].text.strip()
                    cards_yellow = columns[11].text.strip()
                    cards_red = columns[12].text.strip()
                    fouls = columns[13].text.strip()
                    fouled = columns[14].text.strip()
                    offsides = columns[15].text.strip()
                    crosses = columns[16].text.strip()
                    tackles_won = columns[17].text.strip()
                    interceptions = columns[18].text.strip()
                    own_goals = columns[19].text.strip()
                    pens_won = columns[20].text.strip()
                    pens_conceded = columns[21].text.strip()

                    df = df.append({'matchReport_link':matchReport_link,'home_team': home_team,'away_team': away_team,'venue_date': venue_date,'player_team': home_team,
                                'player_name': player_name,'shirtnumber': shirtnumber,  'nationality': nationality, 'position': position,
                                'age': age, 'min_played': min_played, 'goals': goals, 'assists': assists, 'pens_made': pens_made
                               , 'pens_att': pens_att, 'shots': shots, 'shots_on_target': shots_on_target, 'cards_yellow': cards_yellow
                               , 'cards_red': cards_red, 'fouls': fouls, 'fouled': fouled, 'offsides': offsides
                               , 'crosses': crosses, 'tackles_won': tackles_won, 'interceptions': interceptions, 'own_goals': own_goals
                               , 'pens_won': pens_won, 'pens_conceded': pens_conceded}, ignore_index=True)
            # Collecting away team data
            for row in away_table.tbody.find_all('tr'):
                columns = row.find_all('td')
                player_name = row.find_all('a')[0].text

                if(columns != []):
                    shirtnumber = columns[0].text.strip()
                    try:
                        nationality = columns[1].text.split()[1].strip()
                    except:
                        nationality = None
                    position = columns[2].text.strip()
                    try:
                        age = int(columns[3].text.split("-")[0].strip()) + int(columns[3].text.split("-")[1].strip())/365
                    except:
                        age = None
                    min_played = columns[4].text.strip()
                    goals = columns[5].text.strip()
                    assists = columns[6].text.strip()
                    pens_made = columns[7].text.strip()
                    pens_att = columns[8].text.strip()
                    shots = columns[9].text.strip()
                    shots_on_target = columns[10].text.strip()
                    cards_yellow = columns[11].text.strip()
                    cards_red = columns[12].text.strip()
                    fouls = columns[13].text.strip()
                    fouled = columns[14].text.strip()
                    offsides = columns[15].text.strip()
                    crosses = columns[16].text.strip()
                    tackles_won = columns[17].text.strip()
                    interceptions = columns[18].text.strip()
                    own_goals = columns[19].text.strip()
                    pens_won = columns[20].text.strip()
                    pens_conceded = columns[21].text.strip()
                    

                    df = df.append({'matchReport_link':matchReport_link,'home_team': home_team,'away_team': away_team,'venue_date': venue_date,'player_team': away_team,
                                'player_name': player_name,'shirtnumber': shirtnumber,  'nationality': nationality, 'position': position,
                                'age': age, 'min_played': min_played, 'goals': goals, 'assists': assists, 'pens_made': pens_made
                               , 'pens_att': pens_att, 'shots': shots, 'shots_on_target': shots_on_target, 'cards_yellow': cards_yellow
                               , 'cards_red': cards_red, 'fouls': fouls, 'fouled': fouled, 'offsides': offsides
                               , 'crosses': crosses, 'tackles_won': tackles_won, 'interceptions': interceptions, 'own_goals': own_goals
                               , 'pens_won': pens_won, 'pens_conceded': pens_conceded}, ignore_index=True)
            
        
        
        time.sleep(random.randint(1,5))


1  /  624


/var/folders/_k/_rt6thqx6mj63rxtq_q_l7j00000gn/T/ipykernel_30874/1709097389.py:73: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({'matchReport_link':matchReport_link,'home_team': home_team,'away_team': away_team,'venue_date': venue_date,'player_team': home_team,
/var/folders/_k/_rt6thqx6mj63rxtq_q_l7j00000gn/T/ipykernel_30874/1709097389.py:73: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({'matchReport_link':matchReport_link,'home_team': home_team,'away_team': away_team,'venue_date': venue_date,'player_team': home_team,
/var/folders/_k/_rt6thqx6mj63rxtq_q_l7j00000gn/T/ipykernel_30874/1709097389.py:73: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({'matchReport_link':matchReport_l

2  /  624


/var/folders/_k/_rt6thqx6mj63rxtq_q_l7j00000gn/T/ipykernel_30874/1709097389.py:73: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({'matchReport_link':matchReport_link,'home_team': home_team,'away_team': away_team,'venue_date': venue_date,'player_team': home_team,
/var/folders/_k/_rt6thqx6mj63rxtq_q_l7j00000gn/T/ipykernel_30874/1709097389.py:73: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({'matchReport_link':matchReport_link,'home_team': home_team,'away_team': away_team,'venue_date': venue_date,'player_team': home_team,
/var/folders/_k/_rt6thqx6mj63rxtq_q_l7j00000gn/T/ipykernel_30874/1709097389.py:73: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({'matchReport_link':matchReport_l

3  /  624


...

/var/folders/_k/_rt6thqx6mj63rxtq_q_l7j00000gn/T/ipykernel_30874/1709097389.py:73: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({'matchReport_link':matchReport_link,'home_team': home_team,'away_team': away_team,'venue_date': venue_date,'player_team': home_team,
/var/folders/_k/_rt6thqx6mj63rxtq_q_l7j00000gn/T/ipykernel_30874/1709097389.py:73: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({'matchReport_link':matchReport_link,'home_team': home_team,'away_team': away_team,'venue_date': venue_date,'player_team': home_team,
/var/folders/_k/_rt6thqx6mj63rxtq_q_l7j00000gn/T/ipykernel_30874/1709097389.py:73: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({'matchReport_link':matchReport_l

/var/folders/_k/_rt6thqx6mj63rxtq_q_l7j00000gn/T/ipykernel_30874/1709097389.py:125: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({'matchReport_link':matchReport_link,'home_team': home_team,'away_team': away_team,'venue_date': venue_date,'player_team': away_team,
/var/folders/_k/_rt6thqx6mj63rxtq_q_l7j00000gn/T/ipykernel_30874/1709097389.py:125: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({'matchReport_link':matchReport_link,'home_team': home_team,'away_team': away_team,'venue_date': venue_date,'player_team': away_team,
/var/folders/_k/_rt6thqx6mj63rxtq_q_l7j00000gn/T/ipykernel_30874/1709097389.py:125: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({'matchReport_link':matchRepor

624  /  624


/var/folders/_k/_rt6thqx6mj63rxtq_q_l7j00000gn/T/ipykernel_30874/1709097389.py:73: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({'matchReport_link':matchReport_link,'home_team': home_team,'away_team': away_team,'venue_date': venue_date,'player_team': home_team,
/var/folders/_k/_rt6thqx6mj63rxtq_q_l7j00000gn/T/ipykernel_30874/1709097389.py:73: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({'matchReport_link':matchReport_link,'home_team': home_team,'away_team': away_team,'venue_date': venue_date,'player_team': home_team,
/var/folders/_k/_rt6thqx6mj63rxtq_q_l7j00000gn/T/ipykernel_30874/1709097389.py:73: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({'matchReport_link':matchReport_l

/var/folders/_k/_rt6thqx6mj63rxtq_q_l7j00000gn/T/ipykernel_30874/1709097389.py:125: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({'matchReport_link':matchReport_link,'home_team': home_team,'away_team': away_team,'venue_date': venue_date,'player_team': away_team,
/var/folders/_k/_rt6thqx6mj63rxtq_q_l7j00000gn/T/ipykernel_30874/1709097389.py:125: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({'matchReport_link':matchReport_link,'home_team': home_team,'away_team': away_team,'venue_date': venue_date,'player_team': away_team,
/var/folders/_k/_rt6thqx6mj63rxtq_q_l7j00000gn/T/ipykernel_30874/1709097389.py:125: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({'matchReport_link':matchRepor

In [7]:
df

matchReport_link       home_team  \
0      https://fbref.com/en/matches/e62f6e78/Crystal-...  Crystal Palace   
1      https://fbref.com/en/matches/e62f6e78/Crystal-...  Crystal Palace   
2      https://fbref.com/en/matches/e62f6e78/Crystal-...  Crystal Palace   
3      https://fbref.com/en/matches/e62f6e78/Crystal-...  Crystal Palace   
4      https://fbref.com/en/matches/e62f6e78/Crystal-...  Crystal Palace   
...                                                  ...             ...   
18718  https://fbref.com/en/matches/9edb32a3/Leeds-Un...    Leeds United   
18719  https://fbref.com/en/matches/9edb32a3/Leeds-Un...    Leeds United   
18720  https://fbref.com/en/matches/9edb32a3/Leeds-Un...    Leeds United   
18721  https://fbref.com/en/matches/9edb32a3/Leeds-Un...    Leeds United   
18722  https://fbref.com/en/matches/9edb32a3/Leeds-Un...    Leeds United   

         away_team  venue_date     player_team             player_name  \
0          Arsenal  2022-08-05  Crystal Palace         Odsonne Édouard   
1          Arsenal  2022-08-05  Crystal Palace    Jean-Philippe Mateta   
2          Arsenal  2022-08-05  Crystal Palace           Wilfried Zaha   
3          Arsenal  2022-08-05  Crystal Palace             Jordan Ayew   
4          Arsenal  2022-08-05  Crystal Palace            Eberechi Eze   
...            ...         ...             ...                     ...   
18718  Southampton  2023-02-25     Southampton      Kyle Walker-Peters   
18719  Southampton  2023-02-25     Southampton     Armel Bella Kotchap   
18720  Southampton  2023-02-25     Southampton            Jan Bednarek   
18721  Southampton  2023-02-25     Southampton  Ainsley Maitland-Niles   
18722  Southampton  2023-02-25     Southampton            Gavin Bazunu   

      shirtnumber nationality position        age  ... take_ons take_ons_won  \
0              22         FRA       FW  24.550685  ...        2            1   
1              14         FRA       FW  25.104110  ...        0            0   
2              11         CIV       LW  29.734247  ...        5            3   
3               9         GHA    RW,AM  30.898630  ...        9            6   
4              10         ENG       AM  24.101370  ...        4            1   
...           ...         ...      ...        ...  ...      ...          ...   
18718           2         ENG       LB  25.871233  ...        2            2   
18719          37         GER       CB  21.208219  ...        1            0   
18720          35         POL       CB  26.873973  ...        0            0   
18721           3         ENG       RB  25.493151  ...        3            1   
18722          31         IRL       GK  21.013699  ...        0            0   

      crosses fouled fouls offsides own_goals pens_conceded pens_won  \
0         NaN    NaN   NaN      NaN       NaN           NaN      NaN   
1         NaN    NaN   NaN      NaN       NaN           NaN      NaN   
2         NaN    NaN   NaN      NaN       NaN           NaN      NaN   
3         NaN    NaN   NaN      NaN       NaN           NaN      NaN   
4         NaN    NaN   NaN      NaN       NaN           NaN      NaN   
...       ...    ...   ...      ...       ...           ...      ...   
18718     NaN    NaN   NaN      NaN       NaN           NaN      NaN   
18719     NaN    NaN   NaN      NaN       NaN           NaN      NaN   
18720     NaN    NaN   NaN      NaN       NaN           NaN      NaN   
18721     NaN    NaN   NaN      NaN       NaN           NaN      NaN   
18722     NaN    NaN   NaN      NaN       NaN           NaN      NaN   

      tackles_won  
0             NaN  
1             NaN  
2             NaN  
3             NaN  
4             NaN  
...           ...  
18718         NaN  
18719         NaN  
18720         NaN  
18721         NaN  
18722         NaN  

[18723 rows x 44 columns]

In [8]:
df.to_csv("pl_player_stats.csv")

In [9]:
#for index in range(311,len(matchReports_list)):
for index in range(1):
        print(index+1, " / ",len(matchReports_list))
        match_details = dict()
        html = getAndParseURL('https://fbref.com/en/matches/25436a3b/Everton-Aston-Villa-February-25-2023-Premier-League')
        #html = getAndParseURL('https://fbref.com' + matchReports_list[index])
        matchReport_link = ('https://fbref.com' + matchReports_list[index])

        #Scraping the name of the teams and competition
        temp = list()
        for i in html.find_all("div",{"class":"scorebox"}):
            for j in i.find_all("a"):
                temp.append(j.text)
        home_team = temp[0]
        if temp[4] == 'Prev Match':
            away_team = temp[3]
        else:
            away_team = temp[4]

        #Scraping the date and the time of the venue
        el = html.find("span",{"class":"venuetime"})
        venue_date = el['data-venue-date']
        
        table_list = html.find_all('table', class_='stats_table sortable')
        if len(table_list) >= 6:
            home_table = table_list[0]
            away_table = table_list[6]


            # Collecting home team data
            for row in home_table.tbody.find_all('tr'):    
                columns = row.find_all('td')
                player_name = row.find_all('a')[0].text

                if(columns != []):
                    shirtnumber = columns[0].text.strip()
                    try:
                        nationality = columns[1].text.split()[1].strip()
                    except:
                        nationality = None
                    position = columns[2].text.strip()
                    try:
                        age = int(columns[3].text.split("-")[0].strip()) + int(columns[3].text.split("-")[1].strip())/365
                    except:
                        age = None
                    min_played = columns[4].text.strip()
                    goals = columns[5].text.strip()
                    assists = columns[6].text.strip()
                    pens_made = columns[7].text.strip()
                    pens_att = columns[8].text.strip()
                    shots = columns[9].text.strip()
                    shots_on_target = columns[10].text.strip()
                    cards_yellow = columns[11].text.strip()
                    cards_red = columns[12].text.strip()
                    touches = columns[13].text.strip()
                    tackles = columns[14].text.strip()
                    interceptions = columns[15].text.strip()
                    blocks = columns[16].text.strip()
                    xg = columns[17].text.strip()
                    npxg = columns[18].text.strip()
                    xg_assist = columns[19].text.strip()
                    sca = columns[20].text.strip()
                    gca = columns[21].text.strip()
                    passes_completed = columns[22].text.strip()
                    passes = columns[23].text.strip()
                    passes_pct = columns[24].text.strip()
                    progressive_passes = columns[25].text.strip()
                    carries = columns[26].text.strip()
                    progressive_carries = columns[27].text.strip()
                    take_ons = columns[28].text.strip()
                    take_ons_won = columns[29].text.strip()

                    df = df.append({'matchReport_link':matchReport_link,'home_team': home_team,'away_team': away_team,'venue_date': venue_date,'player_team': home_team,
                                    'player_name': player_name,'shirtnumber': shirtnumber,  'nationality': nationality, 'position': position,
                                    'age': age, 'min_played': min_played, 'goals': goals, 'assists': assists, 'pens_made': pens_made
                                   , 'pens_att': pens_att, 'shots': shots, 'shots_on_target': shots_on_target, 'cards_yellow': cards_yellow
                                   , 'cards_red': cards_red, 'touches': touches, 'tackles': tackles, 'interceptions': interceptions
                                   , 'blocks': blocks, 'xg': xg, 'npxg': npxg, 'xg_assist': xg_assist, 'sca': sca
                                   , 'gca': gca, 'passes_completed': passes_completed, 'passes': passes, 'passes_pct': passes_pct
                                   , 'progressive_passes': progressive_passes, 'carries': carries, 'progressive_carries': progressive_carries
                                    , 'take_ons': take_ons, 'take_ons_won': take_ons_won}, ignore_index=True)
            # Collecting away team data
            for row in away_table.tbody.find_all('tr'):
                columns = row.find_all('td')
                player_name = row.find_all('a')[0].text

                if(columns != []):
                    shirtnumber = columns[0].text.strip()
                    try:
                        nationality = columns[1].text.split()[1].strip()
                    except:
                        nationality = None
                    position = columns[2].text.strip()
                    try:
                        age = int(columns[3].text.split("-")[0].strip()) + int(columns[3].text.split("-")[1].strip())/365
                    except:
                        age = None
                    min_played = columns[4].text.strip()
                    goals = columns[5].text.strip()
                    assists = columns[6].text.strip()
                    pens_made = columns[7].text.strip()
                    pens_att = columns[8].text.strip()
                    shots = columns[9].text.strip()
                    shots_on_target = columns[10].text.strip()
                    cards_yellow = columns[11].text.strip()
                    cards_red = columns[12].text.strip()
                    touches = columns[13].text.strip()
                    tackles = columns[14].text.strip()
                    interceptions = columns[15].text.strip()
                    blocks = columns[16].text.strip()
                    xg = columns[17].text.strip()
                    npxg = columns[18].text.strip()
                    xg_assist = columns[19].text.strip()
                    sca = columns[20].text.strip()
                    gca = columns[21].text.strip()
                    passes_completed = columns[22].text.strip()
                    passes = columns[23].text.strip()
                    passes_pct = columns[24].text.strip()
                    progressive_passes = columns[25].text.strip()
                    carries = columns[26].text.strip()
                    progressive_carries = columns[27].text.strip()
                    take_ons = columns[28].text.strip()
                    take_ons_won = columns[29].text.strip()

                    df = df.append({'matchReport_link':matchReport_link,'home_team': home_team,'away_team': away_team,'venue_date': venue_date,'player_team': away_team,
                                'player_name': player_name,'shirtnumber': shirtnumber,  'nationality': nationality, 'position': position,
                                'age': age, 'min_played': min_played, 'goals': goals, 'assists': assists, 'pens_made': pens_made
                               , 'pens_att': pens_att, 'shots': shots, 'shots_on_target': shots_on_target, 'cards_yellow': cards_yellow
                               , 'cards_red': cards_red, 'touches': touches, 'tackles': tackles, 'interceptions': interceptions
                               , 'blocks': blocks, 'xg': xg, 'npxg': npxg, 'xg_assist': xg_assist, 'sca': sca
                               , 'gca': gca, 'passes_completed': passes_completed, 'passes': passes, 'passes_pct': passes_pct
                               , 'progressive_passes': progressive_passes, 'carries': carries, 'progressive_carries': progressive_carries
                                , 'take_ons': take_ons, 'take_ons_won': take_ons_won}, ignore_index=True)
        else:
            home_table = table_list[0]
            away_table = table_list[1]


            # Collecting home team data
            for row in home_table.tbody.find_all('tr'):    
                columns = row.find_all('td')
                player_name = row.find_all('a')[0].text

                if(columns != []):
                    shirtnumber = columns[0].text.strip()
                    try:
                        nationality = columns[1].text.split()[1].strip()
                    except:
                        nationality = None
                    position = columns[2].text.strip()
                    try:
                        age = int(columns[3].text.split("-")[0].strip()) + int(columns[3].text.split("-")[1].strip())/365
                    except:
                        age = None
                    min_played = columns[4].text.strip()
                    goals = columns[5].text.strip()
                    assists = columns[6].text.strip()
                    pens_made = columns[7].text.strip()
                    pens_att = columns[8].text.strip()
                    shots = columns[9].text.strip()
                    shots_on_target = columns[10].text.strip()
                    cards_yellow = columns[11].text.strip()
                    cards_red = columns[12].text.strip()
                    fouls = columns[13].text.strip()
                    fouled = columns[14].text.strip()
                    offsides = columns[15].text.strip()
                    crosses = columns[16].text.strip()
                    tackles_won = columns[17].text.strip()
                    interceptions = columns[18].text.strip()
                    own_goals = columns[19].text.strip()
                    pens_won = columns[20].text.strip()
                    pens_conceded = columns[21].text.strip()

                    df = df.append({'matchReport_link':matchReport_link,'home_team': home_team,'away_team': away_team,'venue_date': venue_date,'player_team': home_team,
                                'player_name': player_name,'shirtnumber': shirtnumber,  'nationality': nationality, 'position': position,
                                'age': age, 'min_played': min_played, 'goals': goals, 'assists': assists, 'pens_made': pens_made
                               , 'pens_att': pens_att, 'shots': shots, 'shots_on_target': shots_on_target, 'cards_yellow': cards_yellow
                               , 'cards_red': cards_red, 'fouls': fouls, 'fouled': fouled, 'offsides': offsides
                               , 'crosses': crosses, 'tackles_won': tackles_won, 'interceptions': interceptions, 'own_goals': own_goals
                               , 'pens_won': pens_won, 'pens_conceded': pens_conceded}, ignore_index=True)
            # Collecting away team data
            for row in away_table.tbody.find_all('tr'):
                columns = row.find_all('td')
                player_name = row.find_all('a')[0].text

                if(columns != []):
                    shirtnumber = columns[0].text.strip()
                    try:
                        nationality = columns[1].text.split()[1].strip()
                    except:
                        nationality = None
                    position = columns[2].text.strip()
                    try:
                        age = int(columns[3].text.split("-")[0].strip()) + int(columns[3].text.split("-")[1].strip())/365
                    except:
                        age = None
                    min_played = columns[4].text.strip()
                    goals = columns[5].text.strip()
                    assists = columns[6].text.strip()
                    pens_made = columns[7].text.strip()
                    pens_att = columns[8].text.strip()
                    shots = columns[9].text.strip()
                    shots_on_target = columns[10].text.strip()
                    cards_yellow = columns[11].text.strip()
                    cards_red = columns[12].text.strip()
                    fouls = columns[13].text.strip()
                    fouled = columns[14].text.strip()
                    offsides = columns[15].text.strip()
                    crosses = columns[16].text.strip()
                    tackles_won = columns[17].text.strip()
                    interceptions = columns[18].text.strip()
                    own_goals = columns[19].text.strip()
                    pens_won = columns[20].text.strip()
                    pens_conceded = columns[21].text.strip()
                    

                    df = df.append({'matchReport_link':matchReport_link,'home_team': home_team,'away_team': away_team,'venue_date': venue_date,'player_team': away_team,
                                'player_name': player_name,'shirtnumber': shirtnumber,  'nationality': nationality, 'position': position,
                                'age': age, 'min_played': min_played, 'goals': goals, 'assists': assists, 'pens_made': pens_made
                               , 'pens_att': pens_att, 'shots': shots, 'shots_on_target': shots_on_target, 'cards_yellow': cards_yellow
                               , 'cards_red': cards_red, 'fouls': fouls, 'fouled': fouled, 'offsides': offsides
                               , 'crosses': crosses, 'tackles_won': tackles_won, 'interceptions': interceptions, 'own_goals': own_goals
                               , 'pens_won': pens_won, 'pens_conceded': pens_conceded}, ignore_index=True)
            
        
        
        time.sleep(random.randint(1,5))


1  /  624


/var/folders/_k/_rt6thqx6mj63rxtq_q_l7j00000gn/T/ipykernel_30874/259383919.py:73: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({'matchReport_link':matchReport_link,'home_team': home_team,'away_team': away_team,'venue_date': venue_date,'player_team': home_team,
/var/folders/_k/_rt6thqx6mj63rxtq_q_l7j00000gn/T/ipykernel_30874/259383919.py:73: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({'matchReport_link':matchReport_link,'home_team': home_team,'away_team': away_team,'venue_date': venue_date,'player_team': home_team,
/var/folders/_k/_rt6thqx6mj63rxtq_q_l7j00000gn/T/ipykernel_30874/259383919.py:73: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({'matchReport_link':matchReport_link

/var/folders/_k/_rt6thqx6mj63rxtq_q_l7j00000gn/T/ipykernel_30874/259383919.py:125: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({'matchReport_link':matchReport_link,'home_team': home_team,'away_team': away_team,'venue_date': venue_date,'player_team': away_team,
/var/folders/_k/_rt6thqx6mj63rxtq_q_l7j00000gn/T/ipykernel_30874/259383919.py:125: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({'matchReport_link':matchReport_link,'home_team': home_team,'away_team': away_team,'venue_date': venue_date,'player_team': away_team,
/var/folders/_k/_rt6thqx6mj63rxtq_q_l7j00000gn/T/ipykernel_30874/259383919.py:125: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append({'matchReport_link':matchReport_l

In [10]:
df

matchReport_link       home_team  \
0      https://fbref.com/en/matches/e62f6e78/Crystal-...  Crystal Palace   
1      https://fbref.com/en/matches/e62f6e78/Crystal-...  Crystal Palace   
2      https://fbref.com/en/matches/e62f6e78/Crystal-...  Crystal Palace   
3      https://fbref.com/en/matches/e62f6e78/Crystal-...  Crystal Palace   
4      https://fbref.com/en/matches/e62f6e78/Crystal-...  Crystal Palace   
...                                                  ...             ...   
18745  https://fbref.com/en/matches/e62f6e78/Crystal-...         Everton   
18746  https://fbref.com/en/matches/e62f6e78/Crystal-...         Everton   
18747  https://fbref.com/en/matches/e62f6e78/Crystal-...         Everton   
18748  https://fbref.com/en/matches/e62f6e78/Crystal-...         Everton   
18749  https://fbref.com/en/matches/e62f6e78/Crystal-...         Everton   

         away_team  venue_date     player_team           player_name  \
0          Arsenal  2022-08-05  Crystal Palace       Odsonne Édouard   
1          Arsenal  2022-08-05  Crystal Palace  Jean-Philippe Mateta   
2          Arsenal  2022-08-05  Crystal Palace         Wilfried Zaha   
3          Arsenal  2022-08-05  Crystal Palace           Jordan Ayew   
4          Arsenal  2022-08-05  Crystal Palace          Eberechi Eze   
...            ...         ...             ...                   ...   
18745  Aston Villa  2023-02-25     Aston Villa           Emi Buendía   
18746  Aston Villa  2023-02-25     Aston Villa          Tyrone Mings   
18747  Aston Villa  2023-02-25     Aston Villa            Ezri Konsa   
18748  Aston Villa  2023-02-25     Aston Villa            Matty Cash   
18749  Aston Villa  2023-02-25     Aston Villa     Emiliano Martínez   

      shirtnumber nationality position        age  ... take_ons take_ons_won  \
0              22         FRA       FW  24.550685  ...        2            1   
1              14         FRA       FW  25.104110  ...        0            0   
2              11         CIV       LW  29.734247  ...        5            3   
3               9         GHA    RW,AM  30.898630  ...        9            6   
4              10         ENG       AM  24.101370  ...        4            1   
...           ...         ...      ...        ...  ...      ...          ...   
18745          10         ARG       FW  26.169863  ...        1            1   
18746           5         ENG       CB  29.956164  ...        1            0   
18747           4         ENG       CB  25.342466  ...        0            0   
18748           2         POL       RB  25.553425  ...        2            1   
18749           1         ARG       GK  30.482192  ...        0            0   

      crosses fouled fouls offsides own_goals pens_conceded pens_won  \
0         NaN    NaN   NaN      NaN       NaN           NaN      NaN   
1         NaN    NaN   NaN      NaN       NaN           NaN      NaN   
2         NaN    NaN   NaN      NaN       NaN           NaN      NaN   
3         NaN    NaN   NaN      NaN       NaN           NaN      NaN   
4         NaN    NaN   NaN      NaN       NaN           NaN      NaN   
...       ...    ...   ...      ...       ...           ...      ...   
18745     NaN    NaN   NaN      NaN       NaN           NaN      NaN   
18746     NaN    NaN   NaN      NaN       NaN           NaN      NaN   
18747     NaN    NaN   NaN      NaN       NaN           NaN      NaN   
18748     NaN    NaN   NaN      NaN       NaN           NaN      NaN   
18749     NaN    NaN   NaN      NaN       NaN           NaN      NaN   

      tackles_won  
0             NaN  
1             NaN  
2             NaN  
3             NaN  
4             NaN  
...           ...  
18745         NaN  
18746         NaN  
18747         NaN  
18748         NaN  
18749         NaN  

[18750 rows x 44 columns]

In [12]:
df.to_csv("pl_player_stats.csv")